### Create similarity features

In this tutorial we will look into another way of deriving features from other features - creating similarity features.

We will create a feature that compares the customer purchase patterns across product groups to all customers purchase patterns. We will first do bucketing at the customer level and at the overall level. Then we will compare the 2 dictionaries with the cosine similarity.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

22:01:28 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


22:01:28 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


22:01:29 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


22:01:29 | INFO     | No catalog activated.


22:01:30 | INFO     | 6 feature lists, 31 features deployed


...

22:01:30 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


22:01:31 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


22:01:31 | INFO     | No catalog activated.


22:01:31 | INFO     | 6 feature lists, 31 features deployed


22:01:32 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

#### Join views 

In [3]:
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

#### Create distribution features across |product groups

In [4]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid) across different ProductGroups.
invoiceitems_view_by_customer_across_productgroup =\
invoiceitems_view.groupby(
    ['GroceryCustomerGuid'], category="ProductGroup"
)

In [5]:
# Create Buckets representing the cumulative TotalCost of item, categorized by ProductGroup,
# for the customer over the past 26 weeks.
# The result is presented as a dictionary where the ProductGroup serves as the key
# and its corresponding sum of item TotalCost for the customer forms the value.
feature_group =\
invoiceitems_view_by_customer_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"
    ],
    windows=["26w"]
)
# Get CUSTOMER_item_TotalCost_across_product_ProductGroups_26w object from feature group.
customer_item_totalcost_across_product_productgroups_26w =\
feature_group["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"]

In [6]:
# Group INVOICEITEMS view across different ProductGroups.
invoiceitems_view_by_overall_across_productgroup =\
invoiceitems_view.groupby([], category="ProductGroup")

In [7]:
# Create Buckets representing the cumulative TotalCost of item, categorized by ProductGroup,
# for ALL customers over the past 26 weeks.
# The result is presented as a dictionary where the ProductGroup serves as the key
# and its corresponding sum of item TotalCost forms the value.
feature_group =\
invoiceitems_view_by_overall_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "OVERALL_item_TotalCost_across_product_ProductGroups_26w"
    ],
    windows=["26w"]
)
# Get OVERALL_item_TotalCost_across_product_ProductGroups_26w object from feature group.
overall_item_totalcost_across_product_productgroups_26w =\
feature_group["OVERALL_item_TotalCost_across_product_ProductGroups_26w"]

#### Derive Similarity feature across entities

In [8]:
# Derive Similarity feature from cosine similarity between
# CUSTOMER_item_TotalCost_across_product_ProductGroups_26w
# and OVERALL_item_TotalCost_across_product_ProductGroups_26w
customer_vs_overall_item_totalcost_across_product_productgroups_26w =\
customer_item_totalcost_across_product_productgroups_26w.cd.cosine_similarity(
        overall_item_totalcost_across_product_productgroups_26w
    )
# Give a name to new feature
customer_vs_overall_item_totalcost_across_product_productgroups_26w.name = \
"CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w"

#### Preview feature

In [9]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [10]:
# Preview CUSTOMER_item_TotalCost_across_product_ProductGroups_26w
customer_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-07-21 12:50:21  dd0c74f0-9ba8-4ca9-bd84-8148095aa38a   
1 2022-11-10 15:57:20  0401635c-e6ab-4525-bb5d-00aba7f6d0c4   
2 2022-08-14 19:00:14  54d86ef6-f9b8-40e2-9162-a60bd1b705db   
3 2022-07-12 08:02:04  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-13 08:15:49  1e866814-e5a6-475d-87e3-b53377cc005b   
5 2023-04-26 16:52:34  48072b52-39cf-452c-8531-02cc4d0fc32e   
6 2023-03-01 11:31:00  081f111a-598b-43ae-a28a-3a5dc3d2a091   
7 2023-01-19 16:33:33  f3415165-754c-40b6-af17-06ef952a3fa1   
8 2023-04-11 19:07:26  d0ea14bf-038a-4ae5-887e-e2d4d68dd8f6   
9 2023-04-10 08:24:27  69d8718e-8c4a-4264-8edf-e0ffc1ef4737   

  CUSTOMER_item_TotalCost_across_product_ProductGroups_26w  
0  {\n  "Adoucissants et Soin du linge": 3.489000...        
1  {\n  "Aide à la Pâtisserie": 4.859999999999999...        
2  {\n  "Adoucissants et Soin du linge": 5.980000...        
3  {\n  "Adoucissants et Soin du linge": 8.880000...        
4  {\n  "Adoucissants et Soin du linge": 2.390000...        
5  {\n  "Aide à la Pâtisserie": 5.340000000000000...        
6  {\n  "Aide à la Pâtisserie": 1.680000000000000...        
7  {\n  "Adoucissants et Soin du linge": 1.731000...        
8  {\n  "Adoucissants et Soin du linge": 2.990000...        
9  {\n  "Aide à la Pâtisserie": 2.280000000000000...

In [11]:
# Preview OVERALL_item_TotalCost_across_product_ProductGroups_26w
overall_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-07-21 12:50:21  dd0c74f0-9ba8-4ca9-bd84-8148095aa38a   
1 2022-11-10 15:57:20  0401635c-e6ab-4525-bb5d-00aba7f6d0c4   
2 2022-08-14 19:00:14  54d86ef6-f9b8-40e2-9162-a60bd1b705db   
3 2022-07-12 08:02:04  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-13 08:15:49  1e866814-e5a6-475d-87e3-b53377cc005b   
5 2023-04-26 16:52:34  48072b52-39cf-452c-8531-02cc4d0fc32e   
6 2023-03-01 11:31:00  081f111a-598b-43ae-a28a-3a5dc3d2a091   
7 2023-01-19 16:33:33  f3415165-754c-40b6-af17-06ef952a3fa1   
8 2023-04-11 19:07:26  d0ea14bf-038a-4ae5-887e-e2d4d68dd8f6   
9 2023-04-10 08:24:27  69d8718e-8c4a-4264-8edf-e0ffc1ef4737   

  OVERALL_item_TotalCost_across_product_ProductGroups_26w  
0  {\n  "Adoucissants et Soin du linge": 1.145020...       
1  {\n  "Adoucissants et Soin du linge": 1.156350...       
2  {\n  "Adoucissants et Soin du linge": 1.145570...       
3  {\n  "Adoucissants et Soin du linge": 1.151100...       
4  {\n  "Adoucissants et Soin du linge": 1.137150...       
5  {\n  "Adoucissants et Soin du linge": 1.213250...       
6  {\n  "Adoucissants et Soin du linge": 1.212720...       
7  {\n  "Adoucissants et Soin du linge": 1.185870...       
8  {\n  "Adoucissants et Soin du linge": 1.224350...       
9  {\n  "Adoucissants et Soin du linge": 1.253590...

In [12]:
# Preview CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w
customer_vs_overall_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-07-21 12:50:21  dd0c74f0-9ba8-4ca9-bd84-8148095aa38a   
1 2022-11-10 15:57:20  0401635c-e6ab-4525-bb5d-00aba7f6d0c4   
2 2022-08-14 19:00:14  54d86ef6-f9b8-40e2-9162-a60bd1b705db   
3 2022-07-12 08:02:04  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-13 08:15:49  1e866814-e5a6-475d-87e3-b53377cc005b   
5 2023-04-26 16:52:34  48072b52-39cf-452c-8531-02cc4d0fc32e   
6 2023-03-01 11:31:00  081f111a-598b-43ae-a28a-3a5dc3d2a091   
7 2023-01-19 16:33:33  f3415165-754c-40b6-af17-06ef952a3fa1   
8 2023-04-11 19:07:26  d0ea14bf-038a-4ae5-887e-e2d4d68dd8f6   
9 2023-04-10 08:24:27  69d8718e-8c4a-4264-8edf-e0ffc1ef4737   

   CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w  
0                                           0.681454                    
1                                           0.751135                    
2                                           0.417760                    
3                                           0.769076                    
4                                           0.532345                    
5                                           0.839560                    
6                                           0.704808                    
7                                           0.823894                    
8                                           0.866171                    
9                                           0.856881

#### Save feature

In [13]:
# Save feature
customer_vs_overall_item_totalcost_across_product_productgroups_26w.save()

Working... |                                        | ▁▃▅ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▂▄▆ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

...

Working... |████████████████████████████████████████| ▂▂▄ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▁▃▅ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▂▄▆ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▃▅▇ 100% in 7s (~0s, 0.2%/

Done! |████████████████████████████████████████| 100% in 6.7s (0.15%/s)         

#### As always, add description and view definition file

In [14]:
# Add description
customer_vs_overall_item_totalcost_across_product_productgroups_26w.update_description(
    "Similarity between the customer and all customers measured by the "
    "Cosine Similarity between the Distribution representing the cumulative"
    " TotalCost of item,  categorized by their respective product's "
    "ProductGroup, over 26w for both entities."
)
# See feature definition file
customer_vs_overall_item_totalcost_across_product_productgroups_26w.definition

'# Generated by SDK version: 0.5.0.dev6\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ItemTable\n\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("64ff1c940d5bfbfb21bce78c"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("64ff1c920d5bfbfb21bce78b"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\njoined_view = item_view.join(\n    dimension_view, on="GroceryProductGuid", how="left", rsuffix=""\n)\ngrouped = joined_view.groupby(\n    by_keys=[], category="ProductGroup"\n).aggregate_over(\n    value_column="TotalCost",\n    method="sum",\n    windows=["26w"],\n    feature_names=["OVERALL_item_TotalCost_across_product_ProductGroups_26w"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["OVERALL_item_TotalCost_across_product_ProductGroups_26w"]\ngrouped_1 = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category="ProductGroup"\n).aggregate_over(\n    value_column="TotalCost",\n    method="sum",\n    windows=["26w"],\n    feature_names=["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_1 = grouped_1["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"]\nfeat_2 = feat_1.cd.cosine_similarity(other=feat)\nfeat_2.name = (\n    "CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w"\n)\noutput = feat_2\noutput.save(_id=ObjectId("64ff1dc2183aab97b493af21"))\n'

### Concepts in this tutorial
- [View Joins](https://docs.featurebyte.com/latest/about/glossary/#view-join)
- [Feature Transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)
- [Cross Aggregate features](https://docs.featurebyte.com/latest/about/glossary/#cross-aggregate-features)

#### SDK reference for
- [Feature.cd.cosine_similarity()](https://docs.featurebyte.com/latest/reference/featurebyte.Feature.cd.cosine_similarity/)